In [1]:
import joblib
import warnings
import numpy as np
import pandas as pd
import random as rd
import datetime as dt
import matplotlib.pyplot as plt
from matplotlib.lines import Line2D
%matplotlib inline

from tabulate import tabulate
from sklearn.preprocessing import StandardScaler
from sklearn.model_selection import train_test_split
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score

from sklearn.linear_model import LinearRegression
from sklearn.neural_network import MLPRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor
warnings.filterwarnings('ignore')

In [2]:
PATH = '.../NeuralRTE/'

MC_data = pd.read_csv(PATH+'data/MC_data.csv', header=0)
MC_data = MC_data.drop(columns="Rd_r")
MC_data

mua   mus     g       Rd
0        1.0    10  0.00  0.27365
1        1.0    10  0.01  0.27191
2        1.0    10  0.02  0.27043
3        1.0    10  0.03  0.26894
4        1.0    10  0.04  0.26723
...      ...   ...   ...      ...
828095  10.0  1000  0.86  0.31530
828096  10.0  1000  0.87  0.30492
828097  10.0  1000  0.88  0.29431
828098  10.0  1000  0.89  0.28200
828099  10.0  1000  0.90  0.26816

[828100 rows x 4 columns]

In [3]:
# Final models (tunned)
regressors = [LinearRegression(fit_intercept=True, positive=False, n_jobs=-1), 
              MLPRegressor(max_iter=1000, hidden_layer_sizes=(100,100,100), solver='adam', learning_rate='adaptive', activation='relu', batch_size=200, alpha=1e-05), 
              DecisionTreeRegressor(criterion='friedman_mse', splitter='best', min_samples_split=2, min_samples_leaf=1, max_features=1.0, max_depth=20), 
              RandomForestRegressor(n_estimators=200, min_samples_split=3, min_samples_leaf=1, max_features=1.0, max_depth=20, bootstrap=True, n_jobs=-1)]
names = ['LinearRegression', 'MLPRegressor', 'DecisionTreeRegressor', 'RandomForestRegressor']

<br>

# Functions:

In [4]:
def printTb(df):
    print(tabulate(df, headers = 'keys', tablefmt = 'fancy_grid', numalign = 'center', floatfmt=".6f"))

In [5]:
def jitter(arr, m=0.0008):
    stdev = m * (max(arr) - min(arr))
    return arr + np.random.randn(len(arr)) * stdev

In [7]:

def recon2D(model, df, i1, i2, i3):
    fig, ax = plt.subplots(1,3, figsize=(51, 16), dpi=650)
    Rd_pred = model.predict(StandardScaler().fit_transform(df.iloc[:,:-1]))
    
    df_ = df.iloc[i1]
    Rd_pred_ = Rd_pred[i1]

    ax[0].scatter(df_['mua'], jitter(df_['Rd']), s=13.0)
    ax[0].scatter(df_['mua'], jitter(Rd_pred_), s=12.0)
    ax[0].set_xlabel('$\mu_{a}$', fontsize = 65)
    ax[0].set_ylabel('$Rd$'     , fontsize = 60, rotation = 0, labelpad=50)
    ax[0].tick_params(axis='both', which='major', labelsize=28)
    ax[0].set_xticks(ticks=np.arange(1,11), labels=[1,2,3,4,5,6,7,8,9,10])
    ax[0].set_ylim(0.0,0.85)

    df_ = df.iloc[i2]
    Rd_pred_ = Rd_pred[i2]

    ax[1].scatter(df_['mus'], jitter(df_['Rd']), s=13.0)
    ax[1].scatter(df_['mus'], jitter(Rd_pred_), s=12.0)
    ax[1].set_xlabel('$\mu_{s}$', fontsize = 65)
    ax[1].tick_params(axis='both', which='major', labelsize=28)
    ax[1].set_xticks(ticks=np.arange(200,1200,200), labels=[200,400,600,800,1000])
    ax[1].set_ylim(0.0,0.85)

    df_ = df.iloc[i3]
    Rd_pred_ = Rd_pred[i3]

    ax[2].scatter(df_['g'], jitter(df_['Rd']), s=18.0)
    ax[2].scatter(df_['g'], jitter(Rd_pred_, m=0.002), s=16.0)
    ax[2].set_xlabel('$g$'      , fontsize = 65)
    ax[2].tick_params(axis='both', which='major', labelsize=28)
    ax[2].set_ylim(0.0,0.85)

    pred = Line2D([0], [0], label='ML', color='orange',linestyle=':',linewidth=3)
    true = Line2D([0], [0], label='MC', color='#1f77b4',linestyle=':',linewidth=3)


    ax[2].legend(handles=[pred,true], loc='lower left', fontsize="40")

    # plt.savefig(PATH+'figures/reconstruction_plot.pdf')
    plt.show()

In [8]:
#A function for evaluating the perfomance of a model on train + test datasets
def evaluate(model, data): 
    X   = data[0]; Y   = data[1]
    X_t = data[2]; Y_t = data[3]

    S = dt.datetime.now()
    model.fit(X,Y)
    Y_p = model.predict(X_t)
    E = dt.datetime.now()
    DUR = round((E-S).total_seconds(), 3)
    
    #Getting our metrics
    MSE  = mean_squared_error(Y_t,Y_p)
    RMSE = np.sqrt(mean_squared_error(Y_t,Y_p))
    MAE  = mean_absolute_error(Y_t,Y_p)
    R2  = r2_score(Y_t,Y_p)
    
    out = pd.DataFrame([{'MSE': MSE, 'RMSE': RMSE, 'MAE': MAE, 'R2': R2, 'Time(s)': DUR}])
    return out, model

<br>

# Evaluation:

In [9]:
# Spliting our data for training (80%) and testing (20%)
train_set, test_set = train_test_split(MC_data, test_size=0.2)
train_set = train_set.reset_index(drop = True)
test_set = test_set.reset_index(drop = True)

In [10]:
#Getting X/y_train/test and apply StandardScaler() on the inputs data (X)
X = train_set.iloc[:,:-1]
Y = train_set.iloc[:, -1]
X = StandardScaler().fit_transform(X)
    
X_t = test_set.iloc[:,:-1]
Y_t = test_set.iloc[:, -1]
X_t = StandardScaler().fit_transform(X_t)

data = [X,Y,X_t,Y_t]

In [11]:
# Evaluate regressors performance
lr_df, lr_model = evaluate(regressors[0], data)
nn_df, nn_model = evaluate(regressors[1], data)
dt_df, dt_model = evaluate(regressors[2], data)
rf_df, rf_model = evaluate(regressors[3], data)

In [12]:
RD_DATA = lr_df
RD_DATA = pd.concat([RD_DATA, nn_df], axis = 0)
RD_DATA = pd.concat([RD_DATA, dt_df], axis = 0)
RD_DATA = pd.concat([RD_DATA, rf_df], axis = 0)
RD_DATA = RD_DATA.set_axis(names, axis = 0)

In [13]:
printTb(RD_DATA.sort_values(['RMSE', 'MAE', 'R2']))

╒═══════════════════════╤══════════╤══════════╤══════════╤══════════╤═══════════╕
│                       │   MSE    │   RMSE   │   MAE    │    R2    │  Time(s)  │
╞═══════════════════════╪══════════╪══════════╪══════════╪══════════╪═══════════╡
│ RandomForestRegressor │ 0.000001 │ 0.000742 │ 0.000524 │ 0.999980 │ 27.551000 │
├───────────────────────┼──────────┼──────────┼──────────┼──────────┼───────────┤
│ MLPRegressor          │ 0.000004 │ 0.001983 │ 0.001263 │ 0.999858 │ 78.795000 │
├───────────────────────┼──────────┼──────────┼──────────┼──────────┼───────────┤
│ DecisionTreeRegressor │ 0.000007 │ 0.002659 │ 0.002372 │ 0.999745 │ 1.204000  │
├───────────────────────┼──────────┼──────────┼──────────┼──────────┼───────────┤
│ LinearRegression      │ 0.003160 │ 0.056217 │ 0.042453 │ 0.885859 │ 0.026000  │
╘═══════════════════════╧══════════╧══════════╧══════════╧══════════╧═══════════╛


<br>

# Reconstuction:

In [15]:
mua_idx = MC_data.index[((MC_data.mua == 1) | (MC_data.mua == 2) | (MC_data.mua == 3) | (MC_data.mua == 4) | (MC_data.mua == 5) |
                         (MC_data.mua == 6) | (MC_data.mua == 7) | (MC_data.mua == 8) | (MC_data.mua == 9) | (MC_data.mua == 10)) & (MC_data.mus == 500)]

mus_idx = MC_data.index[((MC_data.mus == 100) | (MC_data.mus == 200) | (MC_data.mus == 300) | (MC_data.mus == 400) | (MC_data.mus == 500) |
                         (MC_data.mus == 600) | (MC_data.mus == 700) | (MC_data.mus == 800) | (MC_data.mus == 900) | (MC_data.mus == 1000)) & (MC_data.mua == 5)]

g_idx   = MC_data.index[(MC_data.mua == 5) & (MC_data.mus == 500)]

In [16]:
# Linear Regression
recon2D(lr_model, MC_data, mua_idx,mus_idx,g_idx)

In [18]:
# Random Forest
recon2D(rf_model, MC_data, mua_idx,mus_idx,g_idx)

<br>

## Saving...

In [19]:
# joblib.dump(rf_model, "{0}/models/{1}.sav".format(PATH, 'rd_model'))